In [ ]:
import os
import pandas as pd

In [37]:
def merge_csv_files_in_directory(directory,output):
    dfs = []
    for root, _, files in os.walk(directory):
        for file in files:
            if file.endswith('.csv'):
                filepath = os.path.join(root, file)
                df = pd.read_csv(filepath)
                dfs.append(df)
    merged_df = dfs[0]
    
    for df in dfs[1:]:
        merged_df = pd.merge(merged_df, df, on=['ID_RIO', 'coord_TRAMO'], how='inner')
    
    print(merged_df)
    print("Ahora guardamos en local")
    merged_df.to_csv(output, index=False)

In [31]:
def verificar_permisos_directorio(directory):
    # Verificar si el directorio existe
    if not os.path.exists(directory):
        print(f"El directorio {directory} no existe.")
        return False
    
    # Verificar permisos de lectura
    if not os.access(directory, os.R_OK):
        print(f"No tienes permisos de lectura para el directorio {directory}.")
        return False
    
    # Verificar permisos de escritura
    if not os.access(directory, os.W_OK):
        print(f"No tienes permisos de escritura para el directorio {directory}.")
        return False
    
    # Verificar permisos de ejecución
    if not os.access(directory, os.X_OK):
        print(f"No tienes permisos de ejecución para el directorio {directory}.")
        return False
    
    print(f"Tienes permisos completos para acceder al directorio {directory}.")
    return True

In [41]:
import os
import pandas as pd
import numpy as np
from shapely.wkt import loads
from shapely.geometry import LineString
import geopandas as gpd
import time

def calcular_distancias(fich_rios, contaminante_sf, fich_output, contaminante_col):
    for idx, rio in fich_rios.iterrows():
        linestring = rio['WKT']
        geometry = loads(linestring)
        
        for part in geometry.geoms:
            #Se reducen el número de tramos a 3
            coords = list(part.coords)
            coordinates_to_check = [coords[0], coords[len(coords)//2] if len(coords) % 2 != 0 else coords[len(coords)//2 - 1], coords[-1]]
            #print("Coordinates to check:",coordinates_to_check)
            #print(f"Número de tramos del rio simplificados: {len(coordinates_to_check)}")
            for coordinate in coordinates_to_check:
                #print("Calculando el sensor más cercano al punto: ",coordinate)
                distances = []
                for idx, row in contaminante_sf.iterrows():
                    sensor = row.geometry.coords[0]  # Obtenemos las coordenadas del sensor
                    distance = np.sqrt((coordinate[0] - sensor[0]) ** 2 + (coordinate[1] - sensor[1]) ** 2)
                    distances.append(distance)

                min_distance = min(distances)
                min_distance_index = distances.index(min_distance)
                closest_sensor = contaminante_sf.iloc[min_distance_index]

                # Crear un DataFrame con los datos
                data = {
                    'ID_RIO': [rio['PFAFRIO']],
                    'coord_TRAMO': [coordinate],
                    f'valor_{contaminante_col}': [closest_sensor['PromedioDe']]
                }
                info_tramo = pd.DataFrame(data)

                # Agregar datos al archivo CSV y Verificar si el archivo existe
                if os.path.exists(fich_output):
                    header = False
                else:
                    header = True

                # Escribir datos en el archivo CSV
                info_tramo.to_csv(fich_output, mode='a', header=header, index=False)

In [42]:
df_rios_A = pd.read_csv("/Users/silviadelatorre/Desktop/TFG/FICHEROS INPUT/RiosAtlantico.csv")
df_rios_A_gdf = gpd.GeoDataFrame(df_rios_A, geometry=gpd.GeoSeries.from_wkt(df_rios_A['WKT']))
df_fitobentos = pd.read_csv("/Users/silviadelatorre/Desktop/TFG/AGENTES CONTAMINANTES/Fitobentos.csv")
fitobentos_gdf = gpd.GeoDataFrame(df_fitobentos, geometry=gpd.GeoSeries.from_wkt(df_fitobentos['WKT']))
output_folder_a = "/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/ATLANTICO"
output_path = os.path.join(output_folder_a, "Fitobentos.csv")
calcular_distancias(df_rios_A_gdf, fitobentos_gdf,output_path,"Fitobentos")

Coordinates to check: [(823091.6071, 4736100.5283), (807702.0344, 4738426.8291), (805142.39, 4751389.2164)]
Número de tramos del rio simplificados: 3
Coordinates to check: [(803804.7411, 4750624.8265), (804388.9885, 4750402.1017), (804904.6802, 4750049.8105)]
Número de tramos del rio simplificados: 3
Coordinates to check: [(802042.3449, 4750624.8564), (802880.6889, 4750698.3937), (803804.7411, 4750624.8265)]
Número de tramos del rio simplificados: 3
Coordinates to check: [(802442.3183, 4751124.8497), (802638.8478, 4750951.9476), (802879.7924, 4750699.8344)]
Número de tramos del rio simplificados: 3
Coordinates to check: [(800992.4112, 4751199.8984), (801815.947, 4750854.0155), (802779.7979, 4750674.8348)]
Número de tramos del rio simplificados: 3
Coordinates to check: [(802767.2979, 4751612.3485), (803299.905, 4751097.8279), (803804.7411, 4750624.8265)]
Número de tramos del rio simplificados: 3
Coordinates to check: [(813379.2677, 4748862.4455), (809326.679, 4748306.4651), (804954.6776

In [ ]:
# UNIR TABLAS EN UNA SOLA
# Directorios de vertientes
vertientes_directorios = ['/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/ATLANTICO', '/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/MEDITERRANEO']
output_file = ["/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/ATLANTICO/ContaminacionAtlantico.csv","/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/MEDITERRANEO/ContaminacionMediterraneo.csv"]

# Iterar sobre cada vertiente
#for vertiente in vertientes_directorios:
verificar_permisos_directorio('/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/MEDITERRANEO')
'''for salida in output_file:
        print(salida)'''
merge_csv_files_in_directory('/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/MEDITERRANEO',"/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/MEDITERRANEO/ContaminacionMediterraneo.csv")

Tienes permisos completos para acceder al directorio /Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/MEDITERRANEO.
           ID_RIO                  coord_TRAMO  valor_Fosfato  valor_Nitrato  \
0        20011112  (268823.9426, 3990345.4563)          0.025         0.5660   
1        20011112  (268412.6746, 3989667.9248)          0.025         0.7325   
2        20011112  (268348.9132, 3988869.4124)          0.025         0.7325   
3       200111132  (268836.4348, 3989895.4539)          0.025         0.5660   
4       200111132  (268914.5713, 3989544.1179)          0.025         0.5660   
...           ...                          ...            ...            ...   
196006      22184  (287403.1153, 3972411.4271)          0.025         0.5660   
196007      22184  (287423.8732, 3972432.7465)          0.025         0.5660   
196008      22188  (286436.9116, 3973782.7564)          0.025         0.5660   
196009      22188  (286953.5246, 3973394.4594)          0.025   

In [38]:
# UNIR TABLAS EN UNA SOLA
# Directorios de vertientes
vertientes_directorios = ['/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/ATLANTICO', '/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/MEDITERRANEO']
output_file = ["/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/ATLANTICO/ContaminacionAtlantico.csv","/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/MEDITERRANEO/ContaminacionMediterraneo.csv"]

# Iterar sobre cada vertiente
#for vertiente in vertientes_directorios:
verificar_permisos_directorio('/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/MEDITERRANEO')
'''for salida in output_file:
        print(salida)'''
merge_csv_files_in_directory('/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/MEDITERRANEO',"/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/MEDITERRANEO/ContaminacionMediterraneo.csv")

Tienes permisos completos para acceder al directorio /Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/MEDITERRANEO.
           ID_RIO                  coord_TRAMO  valor_Fosfato  valor_Nitrato  \
0        20011112  (268823.9426, 3990345.4563)          0.025         0.5660   
1        20011112  (268412.6746, 3989667.9248)          0.025         0.7325   
2        20011112  (268348.9132, 3988869.4124)          0.025         0.7325   
3       200111132  (268836.4348, 3989895.4539)          0.025         0.5660   
4       200111132  (268914.5713, 3989544.1179)          0.025         0.5660   
...           ...                          ...            ...            ...   
196006      22184  (287403.1153, 3972411.4271)          0.025         0.5660   
196007      22184  (287423.8732, 3972432.7465)          0.025         0.5660   
196008      22188  (286436.9116, 3973782.7564)          0.025         0.5660   
196009      22188  (286953.5246, 3973394.4594)          0.025   

In [ ]:
# UNIR TABLAS EN UNA SOLA
# Directorios de vertientes
vertientes_directorios = ['/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/ATLANTICO', '/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/MEDITERRANEO']
output_file = ["/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/ATLANTICO/ContaminacionAtlantico.csv","/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/MEDITERRANEO/ContaminacionMediterraneo.csv"]

# Iterar sobre cada vertiente
#for vertiente in vertientes_directorios:
verificar_permisos_directorio('/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/MEDITERRANEO')
    '''for salida in output_file:
        print(salida)'''
merged_df = merge_csv_files_in_directory(vertiente,"/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/MEDITERRANEO/ContaminacionMediterraneo.csv")

Tienes permisos completos para acceder al directorio /Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/ATLANTICO.
/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/ATLANTICO/ContaminacionAtlantico.csv
          ID_RIO                  coord_TRAMO  valor_Fosfato  valor_Nitrato  \
0          10034  (823091.6071, 4736100.5283)        0.00560         1.0605   
1          10034  (807702.0344, 4738426.8291)        0.00459         1.5600   
2          10034    (805142.39, 4751389.2164)        0.01748         1.1355   
3          10034    (805142.39, 4751389.2164)        0.01748         1.1355   
4       10034996  (803804.7411, 4750624.8265)        0.01748         1.1355   
...          ...                          ...            ...            ...   
325643  10099922  (267441.0379, 3990306.2624)        0.02500         0.7325   
325644  10099922   (267173.9276, 3989732.971)        0.02500         0.7325   
325645  10099924   (269586.4743, 3991970.456)     

In [ ]:
# UNIR TABLAS EN UNA SOLA
# Directorios de vertientes
vertientes_directorios = ['/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/ATLANTICO', '/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/MEDITERRANEO']
output_file = ["/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/ATLANTICO/ContaminacionAtlantico.csv","/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/MEDITERRANEO/ContaminacionMediterraneo.csv"]

# Iterar sobre cada vertiente
#for vertiente in vertientes_directorios:
verificar_permisos_directorio('/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/MEDITERRANEO')
    '''for salida in output_file:
        print(salida)'''
merged_df = merge_csv_files_in_directory(vertiente,salida)

Tienes permisos completos para acceder al directorio /Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/ATLANTICO.
/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/ATLANTICO/ContaminacionAtlantico.csv
          ID_RIO                  coord_TRAMO  valor_Fosfato  valor_Nitrato  \
0          10034  (823091.6071, 4736100.5283)        0.00560         1.0605   
1          10034  (807702.0344, 4738426.8291)        0.00459         1.5600   
2          10034    (805142.39, 4751389.2164)        0.01748         1.1355   
3          10034    (805142.39, 4751389.2164)        0.01748         1.1355   
4       10034996  (803804.7411, 4750624.8265)        0.01748         1.1355   
...          ...                          ...            ...            ...   
325643  10099922  (267441.0379, 3990306.2624)        0.02500         0.7325   
325644  10099922   (267173.9276, 3989732.971)        0.02500         0.7325   
325645  10099924   (269586.4743, 3991970.456)     

In [ ]:
# UNIR TABLAS EN UNA SOLA
# Directorios de vertientes
vertientes_directorios = ['/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/ATLANTICO', '/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/MEDITERRANEO']
output_file = ["/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/ATLANTICO/ContaminacionAtlantico.csv","/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/MEDITERRANEO/ContaminacionMediterraneo.csv"]

# Iterar sobre cada vertiente
for vertiente in vertientes_directorios:
    verificar_permisos_directorio(vertiente)
    for salida in output_file:
        print(salida)
        merged_df = merge_csv_files_in_directory(vertiente,salida)

Tienes permisos completos para acceder al directorio /Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/ATLANTICO.
/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/ATLANTICO/ContaminacionAtlantico.csv
          ID_RIO                  coord_TRAMO  valor_Fosfato  valor_Nitrato  \
0          10034  (823091.6071, 4736100.5283)        0.00560         1.0605   
1          10034  (807702.0344, 4738426.8291)        0.00459         1.5600   
2          10034    (805142.39, 4751389.2164)        0.01748         1.1355   
3          10034    (805142.39, 4751389.2164)        0.01748         1.1355   
4       10034996  (803804.7411, 4750624.8265)        0.01748         1.1355   
...          ...                          ...            ...            ...   
325643  10099922  (267441.0379, 3990306.2624)        0.02500         0.7325   
325644  10099922   (267173.9276, 3989732.971)        0.02500         0.7325   
325645  10099924   (269586.4743, 3991970.456)     

In [ ]:
# UNIR TABLAS EN UNA SOLA
# Directorios de vertientes
vertientes_directorios = ['/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/ATLANTICO', '/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/MEDITERRANEO']
output_file = ["/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/ATLANTICO/ContaminacionAtlantico.csv","/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/MEDITERRANEO/ContaminacionMediterraneo.csv"]

# Iterar sobre cada vertiente
for vertiente in vertientes_directorios:
    verificar_permisos_directorio(vertiente)
    for salida in output_file:
        print(salida)
        merged_df = merge_csv_files_in_directory(vertiente,salida)

Tienes permisos completos para acceder al directorio /Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/ATLANTICO.
/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/ATLANTICO/ContaminacionAtlantico.csv
          ID_RIO                  coord_TRAMO  valor_Fosfato  valor_Nitrato  \
0          10034  (823091.6071, 4736100.5283)        0.00560         1.0605   
1          10034  (807702.0344, 4738426.8291)        0.00459         1.5600   
2          10034    (805142.39, 4751389.2164)        0.01748         1.1355   
3          10034    (805142.39, 4751389.2164)        0.01748         1.1355   
4       10034996  (803804.7411, 4750624.8265)        0.01748         1.1355   
...          ...                          ...            ...            ...   
325643  10099922  (267441.0379, 3990306.2624)        0.02500         0.7325   
325644  10099922   (267173.9276, 3989732.971)        0.02500         0.7325   
325645  10099924   (269586.4743, 3991970.456)     

In [ ]:
#CONCATENAR FICHEROS DE LAS VERTIENTS
output = "/Users/silviadelatorre/Desktop/TFG/PFG/Results/VALORES CONTAMINACION/ValoresContaminación.csv"
